In [1]:
# Useful starting lines
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
from implementations import *
%load_ext autoreload
%autoreload 2

In [2]:
def standardize(tx):
    mean = np.mean(tx, axis=0)
    std = np.std(tx, axis=0)
    tx = (tx-mean)/std
    return tx, mean, std

# function that add new features 
#def build_poly(x, degree):
 #   """polynomial basis functions for input data x, for j=1 up to j=degree."""
  #  phi=np.zeros((x.shape[0],(degree+1)*x.shape[1]))
   # for j in range(degree+1):
    #        phi[:,j*x.shape[1]:(j+1)*x.shape[1]]=x**j
    #return phi

def build_k_indices(y, k_fold, seed):
    """build k indices for k-fold."""
    num_row = y.shape[0]
    interval = int(num_row / k_fold)
    np.random.seed(seed)
    indices = np.random.permutation(num_row)
    k_indices = [indices[k * interval: (k + 1) * interval]
                 for k in range(k_fold)]
    return np.array(k_indices)

def gamma_RLR(y, x, k_fold, lambda_, initial_w, max_iters, gamma, seed=1):
    loss_tr = [] 
    loss_te = []
    ws = []
    k_indices = build_k_indices(y, k_fold, seed)
    plt.figure(figsize=(16,2))
    if not isinstance(gamma,float):
        gamma = np.linspace(gamma[0],gamma[1],max_iters)
    for k in range(k_fold):
        # ***************************************************
        # get k'th subgroup in test, others in train
        # ***************************************************
        idx_tr = (np.delete(k_indices, k, 0)).flatten()
        idx_te = k_indices[k]
        x_tr, y_tr = x[idx_tr], y[idx_tr]
        x_te, y_te = x[idx_te], y[idx_te]
        # ***************************************************
        # calculate the loss for train and test data
        # ***************************************************
        w = initial_w
        loss_local = []
        for i in range(max_iters):
            if not isinstance(gamma,float):
                w, loss = reg_logistic_regression(y_tr, x_tr, lambda_, w, 1, gamma[i],'GD')
            else:
                w, loss = reg_logistic_regression(y_tr, x_tr, lambda_, w, 1, gamma,'GD')
            loss_local.append(loss)
        plt.subplot(100+k_fold*10+k+1)
        plt.plot(loss_local)
        plt.title('k: {}/{}'.format(k+1,k_fold))
        plt.xlabel('iterations')
        plt.ylabel('error')
        loss_tr.append(loss)
        loss_te.append(logistic_loss(y_te, x_te, w) + 0.5*lambda_*w.dot(w))
        ws.append(w)
    plt.show()
    var_tr = np.var(loss_tr)
    var_te = np.var(loss_te)
    loss_tr = np.mean(loss_tr)
    loss_te = np.mean(loss_te)
    ws = np.mean(np.asarray(ws), axis=0)
    return loss_tr, loss_te, var_tr, var_te, ws

def cross_validation_RLR(y, x, k_fold, lambda_, initial_w, max_iters, gamma, seed=1):
    loss_tr = [] 
    loss_te = []
    ws = []
    k_indices = build_k_indices(y, k_fold, seed)
    if not isinstance(gamma,float):
        gamma = np.linspace(gamma[0],gamma[1],max_iters)
    for k in range(k_fold):
        # ***************************************************
        # get k'th subgroup in test, others in train
        # ***************************************************
        idx_tr = (np.delete(k_indices, k, 0)).flatten()
        idx_te = k_indices[k]
        x_tr, y_tr = x[idx_tr], y[idx_tr]
        x_te, y_te = x[idx_te], y[idx_te]
        # ***************************************************
        # calculate the loss for train and test data
        # ***************************************************
        w = initial_w
        for i in range(max_iters):
            if not isinstance(gamma,float):
                w, loss = reg_logistic_regression(y_tr, x_tr, lambda_, w, 1, gamma[i],'GD')
            else:
                w, loss = reg_logistic_regression(y_tr, x_tr, lambda_, w, 1, gamma,'GD')
#             print('run {}/{} - loss: {}'.format(i*print_interval,max_iters,loss))
        loss_tr.append(loss)
        loss_te.append(logistic_loss(y_te, x_te, w) + 0.5*lambda_*w.dot(w))
        ws.append(w)
    var_tr = np.var(loss_tr)
    var_te = np.var(loss_te)
#     print(['train errors: {:.7f}'.format(i) for i in loss_tr])
#     print(['test errors:  {:.7f}'.format(i) for i in loss_te])
    loss_tr = np.mean(loss_tr)
    loss_te = np.mean(loss_te)
    ws = np.mean(np.asarray(ws), axis=0)
    return loss_tr, loss_te, var_tr, var_te, ws


# First : exploring the data

We'll need to have a look at what the data is, how it is distributed for the different features, and start to get an intuition about what methods might work better for analysis and prediction later.

## Load the training data into feature matrix, class labels, and event ids:

In [3]:
from proj1_helpers import *
DATA_TRAIN_PATH = '../data/train.csv' 
y, tX, ids = load_csv_data(DATA_TRAIN_PATH)

In [4]:
# testing methods work
# initial_w = np.ones(tX.shape[1])
# max_iters = 100
# gamma = 0.1
# lambda_ = 0.1
# print('least_squares_GD')
# print(least_squares_GD(y, tX, initial_w, max_iters, gamma))
# print('least_squares_SGD')
# print(least_squares_SGD(y, tX, initial_w, max_iters, gamma))
# print('least_squares')
# print(least_squares(y, tX))
# print('ridge_regression')
# print(ridge_regression(y, tX, lambda_))
# print('logistic_regression SGD')
# print(logistic_regression(y, tX, initial_w, max_iters, gamma, 'SGD'))
# print('logistic_regression GD')
# print(logistic_regression(y, tX, initial_w, max_iters, gamma, 'GD'))
# print('reg_logistic_regression SGD')
# print(reg_logistic_regression(y, tX, lambda_, initial_w, max_iters, gamma, 'SGD'))
# print('reg_logistic_regression GD')
# # print(reg_logistic_regression(y, tX, lambda_, initial_w, max_iters, gamma, 'GD'))
# print('logistic_regression_newton')
# print(logistic_regression_newton(y[:100], tX[:100], initial_w, max_iters, gamma))
# print('reg_logistic_regression_newton')
# print(reg_logistic_regression_newton(y[:100], tX[:100], lambda_, initial_w, max_iters, gamma))

In [5]:
# remove features with error values
y_jet = []
tx_jet = []
mean = []
std = []
# filtering according to undefinition due to jet number
idx_set = [np.array([0,1,2,3,7,10,11,13,14,15,16,17,18,19,20,21]),
           np.array([0,1,2,3,7,8,9,10,11,13,14,15,16,17,18,19,20,21,23,24,25,29]),
           np.array([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,23,24,25,26,27,28,29]),
           np.array([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,23,24,25,26,27,28,29]),
           np.array([1,2,3,7,10,11,13,14,15,16,17,18,19,20,21]),
           np.array([1,2,3,7,8,9,10,11,13,14,15,16,17,18,19,20,21,23,24,25,29]),
           np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,23,24,25,26,27,28,29]),
           np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,23,24,25,26,27,28,29])]
for jet in range(4):
    idx_jet = (tX[:,22]==jet) & (tX[:,0]!=-999)
    y_jet.append(y[idx_jet])
#     tx_jet.append(tX[idx_jet][:,idx_set[jet]])
    tx_i, mean_i, std_i = standardize(tX[idx_jet][:,idx_set[jet]])
    tx_jet.append(tx_i)
    mean.append(mean_i)
    std.append(std_i)
for jet in range(4):
    idx_jet = tX[:,22]==jet
    y_jet.append(y[idx_jet])
#     tx_jet.append(tX[idx_jet][:,idx_set[jet]])
    tx_i, mean_i, std_i = standardize(tX[idx_jet][:,idx_set[jet+4]])
    tx_jet.append(tx_i)
    mean.append(mean_i)
    std.append(std_i)

for jet in range(8):
    print('Jet {:} shape is {:}'.format(jet,tx_jet[jet].shape))

Jet 0 shape is (73790, 16)
Jet 1 shape is (69982, 22)
Jet 2 shape is (47427, 29)
Jet 3 shape is (20687, 29)
Jet 4 shape is (99913, 15)
Jet 5 shape is (77544, 21)
Jet 6 shape is (50379, 28)
Jet 7 shape is (22164, 28)


In [6]:
# print("Overall: s: ",np.sum(y==1),", b: ",np.sum(y==-1)," ,total:",len(y))
# for jet in range(8):
#     print('Jet {:}: s: {:}, b: {:} ,total: {:}'.format(jet, np.sum(y_jet[jet]==1),np.sum(y_jet[jet]==-1),len(y_jet[jet])))
#     for n,feat in enumerate(idx_set[jet]):
#         plt.figure(figsize=(20,1))
#         plt.subplot(131)
#         plt.hist([tx_jet[jet][y_jet[jet]==1,n],tx_jet[jet][y_jet[jet]==-1,n]], 50, density=True, histtype='bar', stacked=True)
#         plt.legend(['s','b'])
#         plt.title('Feature '+str(feat))
#         plt.subplot(132)
#         plt.title('s histogram feature '+str(feat))
#         plt.hist(tx_jet[jet][y_jet[jet]==1,n], 50, density=True, histtype='bar', stacked=True)
#         plt.subplot(133)
#         plt.title('b histogram feature '+str(feat))
#         plt.hist(tx_jet[jet][y_jet[jet]==-1,n], 50, density=True, histtype='bar', stacked=True)    
#         plt.show()

# Actual predictions start from here

After having looked at the data we will now do some actual predictions using different models andd parameters.

In [7]:
# for y_i in y_jet:
#     y_i[y_i==-1] = 0
# max_iters = 300
# k_fold = 5
# gamma = (5e-5,1e-8)
# lambdas = np.logspace(-2, 0, 31)
# seeds = 5

In [8]:
# # Regularized logistic regression
# lambda_  = 0
# gamma = (5e-5,1e-8)
# # gamma = 5e-5
# loss_tr = np.zeros(8)
# loss_te = np.zeros(8)
# for i in range(8):
#     tx_i = tx_jet[i]
#     y_i = y_jet[i]
#     initial_w = np.zeros(tx_i.shape[1])
#     loss_tr[i],loss_te[i],_,_,_ = gamma_RLR(y_i, tx_i, k_fold, lambda_, initial_w, max_iters, gamma)
#     print('set {:} -\n train_loss: {:.6f}, test_loss: {:.6f}'.format(i,loss_tr[i],loss_te[i]))


In [9]:
# # Regularized logistic regression
# loss_tr = np.zeros((8,len(lambdas),seeds))
# loss_te = np.zeros((8,len(lambdas),seeds))
# var_tr = np.zeros((8,len(lambdas),seeds))
# var_te = np.zeros((8,len(lambdas),seeds))
# for i in range(8):
#     tx_i = tx_jet[i]
#     y_i = y_jet[i]
#     for l,lambda_ in enumerate(lambdas):
#         for s in range(seeds):
#             initial_w = np.zeros(tx_i.shape[1])
#             loss_tr[i,l,s],loss_te[i,l,s], var_tr[i,l,s], var_te[i,l,s], ws = cross_validation_RLR(y_i, tx_i, k_fold, lambda_, initial_w, max_iters, gamma,s+1)
#             print('set {:} seed {:} lambda {:.2f} -\n train_loss: {:.6f}, test_loss: {:.6f}, train_var: {:.6f}, test_var: {:.6f}'.format(i,s,lambda_,loss_tr[i,l,s],loss_te[i,l,s], var_tr[i,l,s], var_te[i,l,s]))
# #         initial_w = np.zeros(tx_i.shape[1])
# #         loss_tr[i,l],loss_te[i,l], var_tr[i,l], var_te[i,l], ws = cross_validation_RLR(y_i, tx_i, k_fold, lambda_, initial_w, max_iters, gamma,s)
# #         print('set {:} lambda {:} -\n train_loss: {:.6f}, test_loss: {:.6f}, train_var: {:.6f}, test_var: {:.6f}'.format(i,lambda_,loss_tr[i,l,0],loss_te[i,l,0], var_tr[i,l,0], var_te[i,l,0]))

In [10]:
# for i in range(8):
#     plt.figure(figsize=(16,3))
#     plt.subplot(121)
#     for s in range(seeds):
#         plt.semilogx(lambdas,loss_tr[i][:,s])
# #         plt.semilogx(lambdas,loss_te[i][:,s])
# #     plt.semilogx(lambdas,np.mean(loss_tr[i],axis=1), 'b')
# #     plt.semilogx(lambdas,np.mean(loss_te[i],axis=1), 'r')
#     plt.title('Train and Test Loss of Features set '+str(i))
#     plt.xlabel('lambda')
#     plt.ylabel('error')
#     plt.subplot(122)
# #     for s in range(seeds):
# #         plt.semilogx(lambdas,var_tr[i][:,s])
# #         plt.semilogx(lambdas,var_te[i][:,s])
#     plt.semilogx(lambdas,np.mean(var_tr[i],axis=1))
#     plt.semilogx(lambdas,np.mean(var_te[i],axis=1))
#     plt.title('Train and Test Loss Variations of Features set '+str(i))
#     plt.xlabel('lambda')
#     plt.ylabel('error')
#     plt.show()

In [11]:
# for i in range(8):
#     print('Average Loss for set {} is: train: {}, test: {}'.format(i,np.mean(loss_tr[i]),np.mean(loss_te[i])))
    
# # print(gammas[4])

In [12]:
# for i,var in enumerate(var_te):
#     plt.figure(figsize=(16,6))
#     plt.subplot(121)
#     for seed in range(seeds):
#         plt.semilogx(lambdas,loss_te[i][seed], 'c')
#     plt.semilogx(lambdas,np.mean(loss_te[i],axis=0),'b')
#     plt.title('Loss of Features set '+str(i))
#     plt.xlabel('lambda')
#     plt.ylabel('error')
#     plt.subplot(122)
#     for seed in range(seeds):
#         plt.semilogx(lambdas,var[seed])
#     plt.title('Variation of Loss of Features set '+str(i))
#     plt.xlabel('lambda')
#     plt.ylabel('variation')
#     plt.show()

In [13]:
# for i,var in enumerate(var_te):
#     plt.figure(figsize=(16,6))
#     plt.subplot(121)
#     plt.pcolor(loss_te[i])
#     plt.colorbar()
#     plt.title('Loss of Features set '+str(i))
#     plt.xlabel('gamma')
#     plt.ylabel('lambda')
#     plt.subplot(122)
#     plt.pcolor(np.log10(var))
#     plt.colorbar()
#     plt.title('Variation of Features set '+str(i))
#     plt.xlabel('gamma')
#     plt.ylabel('lambda')
#     plt.show()

In [17]:
# actual model generation
for y_i in y_jet:
    y_i[y_i==-1] = 0
max_iter = 500
lambda_ = 0.1
gamma = np.linspace(5e-5,1e-7,max_iters)

ws = []

for i in range(8):
    tx_i = tx_jet[i]
    y_i = y_jet[i]
    w = np.zeros(tx_jet[i].shape[1])
    for iter in range(max_iter):
        w, loss = reg_logistic_regression(y_i, tx_i, lambda_, w, 1, gamma[iter],'GD')
    ws.append(w)

# Save prediction ouput in csv format for submission:

In [18]:
DATA_TEST_PATH = '../data/test.csv'
_, tX_test, ids_test = load_csv_data(DATA_TEST_PATH)

In [30]:
#split data
y_pred = np.zeros(len(ids_test))
idx_test = []
for i,tx_i in enumerate(tX_test):
    set_i = int(tx_i[22] + 4*(tx_i[0]==-999))
    y_i = np.sign(1/(1+np.exp(-np.clip(tx_i[idx_set[set_i]].dot(ws[set_i]),-350,350)))-0.5)
    y_pred[i] = y_i
y_pred[y_pred==0.0] = -1.0

-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1

-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.

1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.

-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.

-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0

...

-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.

-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0

1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.

1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
1.

-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
1.0
1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
1.0
-1.0
-1.0
1.0
-1.0
1.0
-1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
-1.0
-1.0
-1.0
-1.0
-1.0
1.0
1.0
1.0
1.0
-1.0
1.0
1.0
1.0


In [31]:
OUTPUT_PATH = '../data/results.csv'
# y_pred = predict_labels(weights, tX_test)
create_csv_submission(ids_test, y_pred, OUTPUT_PATH)